# Data imputation

We first keep only the year in the dates for each song. Then, for the songs without dates, we impute the data using three methods:
1. We impute using the album: if one song in the album has a date, then we assign that date to all the other songs in the album
2. We impute using the artist: artists have a couple of songs with dates. We take the average of those dates and impute the average to the missing values of songs from that artist
3. We impute using the pid: each song belongs to several playlists. Each playlist has several songs that have dates. Assume song 0 belongs to playlists 1,2,3,4,5. Then, we take the average of the dates in playlists 1,2,3,4,5. Then song 0 will have 5 dates associated with it, likely different. So we take the average of those 5 dates, and impute that value as the date of the song. 

To verify that our imputation gives good results, we can take the dataset with the newly imputed values and remove the dates that we already had from the beginning, from the original dataset, call them 'original dates'. Then we will use our imputation method to impute the dates for those songs that had dates from the beginning and compare them with the 'original dates'. The goal is to get an error of less than 10 years, i.e. our imputed dates are less than 10 years away from the original date.

From first checks on a couple songs, we find that our imputed dates are about 5 years away from the real dates of the songs. Hence, we can assume that our imputation is correct. 

This way, we can use the date as another predictor in our recommendation models.

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

In [2]:
df = pd.read_csv("playlists_feat.csv")
# df

## Checking the number of NA's

In [3]:
# percentage of NA's
print(len(df[df['Date'].isna()]))
len(df[df['Date'].isna()]) / len(df)

569067


0.7032672743630558

## Keeping only the year

In [4]:
# keeping only the year for the date
df1 = df.copy()
mask = df1['Date'].notna()
mask_condition = df1.loc[mask, 'Date'].str.len() != 4
df1.loc[mask & mask_condition, 'Date'] = pd.to_datetime(df1.loc[mask & mask_condition, 'Date']).dt.year

/var/folders/pq/69vgl51s55vfkk_hk7bl60x00000gn/T/ipykernel_71497/2025641396.py:5: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  df1.loc[mask & mask_condition, 'Date'] = pd.to_datetime(df1.loc[mask & mask_condition, 'Date']).dt.year


In [5]:
# check
df[df['Track']=='Against The Wind']['Date']

3382      2/25/80
41731     2/25/80
48117     2/25/80
49444     2/25/80
218937    2/25/80
268035    2/25/80
428593    2/25/80
546373    2/25/80
576132    2/25/80
636324    2/25/80
779129    2/25/80
Name: Date, dtype: object

In [6]:
df1[df1['Track']=='Against The Wind']['Date']

3382      1980
41731     1980
48117     1980
49444     1980
218937    1980
268035    1980
428593    1980
546373    1980
576132    1980
636324    1980
779129    1980
Name: Date, dtype: object

# Imputing the date for the missing values

In [7]:
df1.sort_values(by='Album')

Track URI       Track             Artist  \
220239  spotify:track:4N4CHJqFZHyB7SBUuSFu1y  Mrs. Right  Mindless Behavior   
299169  spotify:track:4N4CHJqFZHyB7SBUuSFu1y  Mrs. Right  Mindless Behavior   
57436   spotify:track:4N4CHJqFZHyB7SBUuSFu1y  Mrs. Right  Mindless Behavior   
639851  spotify:track:4N4CHJqFZHyB7SBUuSFu1y  Mrs. Right  Mindless Behavior   
451916  spotify:track:4N4CHJqFZHyB7SBUuSFu1y  Mrs. Right  Mindless Behavior   
...                                      ...         ...                ...   
227173  spotify:track:0tgVpDi06FyKpA1z0VMD4v     Perfect         Ed Sheeran   
582403  spotify:track:0tgVpDi06FyKpA1z0VMD4v     Perfect         Ed Sheeran   
107907  spotify:track:44AH8XwgrebHvQAZJbSrsV     P.T.S.D           Scarlxrd   
107930  spotify:track:44AH8XwgrebHvQAZJbSrsV     P.T.S.D           Scarlxrd   
107931  spotify:track:44AH8XwgrebHvQAZJbSrsV     P.T.S.D           Scarlxrd   

          Album Date  Duration            Genre  Danceability  Energy   Key  \
220239  #1 Girl  NaN    248187              RnB         0.439   0.753   0.0   
299169  #1 Girl  NaN    248187              RnB         0.439   0.753   0.0   
57436   #1 Girl  NaN    248187              RnB         0.439   0.753   0.0   
639851  #1 Girl  NaN    248187              RnB         0.439   0.753   0.0   
451916  #1 Girl  NaN    248187              RnB         0.439   0.753   0.0   
...         ...  ...       ...              ...           ...     ...   ...   
227173        ÷  NaN    263400              Pop         0.599   0.448   8.0   
582403        ÷  NaN    263400              Emo         0.599   0.448   8.0   
107907    スカー藩主  NaN    307905        Dark Trap         0.473   0.772  10.0   
107930    スカー藩主  NaN    307905  Underground Rap         0.473   0.772  10.0   
107931    スカー藩主  NaN    307905       Trap Metal         0.473   0.772  10.0   

        ...  Valence    Tempo  Time Signature    Playlist  Num_Tracks  \
220239  ...    0.538  190.678             5.0    car jams         104   
299169  ...    0.538  190.678             5.0        Tops          58   
57436   ...    0.538  190.678             5.0        2010          49   
639851  ...    0.538  190.678             5.0        good          24   
451916  ...    0.538  190.678             5.0  THROW BACK          15   
...     ...      ...      ...             ...         ...         ...   
227173  ...    0.168  190.100             3.0   Serenity          246   
582403  ...    0.168  190.100             3.0  chill out           28   
107907  ...    0.303  130.320             4.0    MAD TING          27   
107930  ...    0.303  130.320             4.0    MAD TING          27   
107931  ...    0.303  130.320             4.0    MAD TING          27   

        Num_Albums  Num_Artists  Follow  Collab     Pid  
220239          53           35       1   False  106503  
299169          51           47       2   False  111315  
57436           39           25       1   False   11611  
639851          10            7       1   False  132373  
451916          14           13       2   False  120848  
...            ...          ...     ...     ...     ...  
227173          75           61       1   False  106970  
582403          21           13       1   False  128813  
107907          14           11       1   False   14661  
107930          14           11       1   False   14661  
107931          14           11       1   False   14661  

[809176 rows x 26 columns]

### Converting the dates into integers

In [8]:
# Select non-NaN values in the 'Date' column
non_nan_dates = df1['Date'].notna()

# Set the non-NaN values to integer type
df1.loc[non_nan_dates, 'Date'] = df1.loc[non_nan_dates, 'Date'].astype(int).round()

## From Album

In [9]:
# Group by 'Album'  and 'Artist'
grouped_df = df1.groupby(['Album', 'Artist'])

# Iterate through groups and print each group with 'Date'
for name, group in grouped_df:
    print(f"Album: {name}")
    print(group[['Track', 'Artist', 'Album', 'Date']])
    print('\n')

Album: ('#1 Girl', 'Mindless Behavior')
             Track             Artist    Album Date
57436   Mrs. Right  Mindless Behavior  #1 Girl  NaN
159511  Mrs. Right  Mindless Behavior  #1 Girl  NaN
164703  Mrs. Right  Mindless Behavior  #1 Girl  NaN
220239  Mrs. Right  Mindless Behavior  #1 Girl  NaN
237347  Mrs. Right  Mindless Behavior  #1 Girl  NaN
299169  Mrs. Right  Mindless Behavior  #1 Girl  NaN
451916  Mrs. Right  Mindless Behavior  #1 Girl  NaN
556051  Mrs. Right  Mindless Behavior  #1 Girl  NaN
582367  Mrs. Right  Mindless Behavior  #1 Girl  NaN
633966  Mrs. Right  Mindless Behavior  #1 Girl  NaN
639851  Mrs. Right  Mindless Behavior  #1 Girl  NaN
686297  Mrs. Right  Mindless Behavior  #1 Girl  NaN
719168  Mrs. Right  Mindless Behavior  #1 Girl  NaN
799374  Mrs. Right  Mindless Behavior  #1 Girl  NaN


Album: ('#CoolUrbanNewTalent', 'Etta Bond')
             Track     Artist                Album Date
681080  Feels Like  Etta Bond  #CoolUrbanNewTalent  NaN
725133  Feels Like  Et

In [10]:
# Filter albums with at least one non-null date
albums_with_dates = df1.dropna(subset=['Date']).groupby(['Album', 'Artist']).size().index

# Group by 'Album' and 'Artist' for filtered albums
filtered_grouped_df = df1[df1.set_index(['Album', 'Artist']).index.isin(albums_with_dates)].groupby(['Album', 'Artist'])

# Iterate through filtered groups and print each group with 'Date'
for (album, artist), group in filtered_grouped_df:
    print(f"Album: {album}, Artist: {artist}")
    print(group[['Track', 'Artist', 'Album', 'Date']])
    print('\n')

Album: #SELFIE, Artist: The Chainsmokers
          Track            Artist    Album  Date
11816   #SELFIE  The Chainsmokers  #SELFIE  2014
16313   #SELFIE  The Chainsmokers  #SELFIE  2014
30969   #SELFIE  The Chainsmokers  #SELFIE  2014
33911   #SELFIE  The Chainsmokers  #SELFIE  2014
40439   #SELFIE  The Chainsmokers  #SELFIE  2014
...         ...               ...      ...   ...
796177  #SELFIE  The Chainsmokers  #SELFIE  2014
797552  #SELFIE  The Chainsmokers  #SELFIE  2014
801758  #SELFIE  The Chainsmokers  #SELFIE  2014
804629  #SELFIE  The Chainsmokers  #SELFIE  2014
805047  #SELFIE  The Chainsmokers  #SELFIE  2014

[156 rows x 4 columns]


Album: '74 Jailbreak, Artist: AC/DC
            Track Artist          Album  Date
94716   Jailbreak  AC/DC  '74 Jailbreak  1984
279254  Jailbreak  AC/DC  '74 Jailbreak  1984
572582  Jailbreak  AC/DC  '74 Jailbreak  1984
580193  Jailbreak  AC/DC  '74 Jailbreak  1984
784350  Jailbreak  AC/DC  '74 Jailbreak  1984


Album: '90s Soul Number 1's, Ar

In [11]:
# Define a function to impute missing dates within each group
def impute_dates(group):
    group['Date'] = group['Date'].fillna(group['Date'].max())
    return group

# Apply the impute_dates function to each group
filtered = grouped_df.apply(impute_dates)
filtered

Track URI  \
Album   Artist                                                           
#1 Girl Mindless Behavior 57436   spotify:track:4N4CHJqFZHyB7SBUuSFu1y   
                          159511  spotify:track:4N4CHJqFZHyB7SBUuSFu1y   
                          164703  spotify:track:4N4CHJqFZHyB7SBUuSFu1y   
                          220239  spotify:track:4N4CHJqFZHyB7SBUuSFu1y   
                          237347  spotify:track:4N4CHJqFZHyB7SBUuSFu1y   
...                                                                ...   
÷       Ed Sheeran        808557  spotify:track:7qiZfU4dY1lWllzX7mPBI3   
                          808851  spotify:track:7qiZfU4dY1lWllzX7mPBI3   
スカー藩主   Scarlxrd          107907  spotify:track:44AH8XwgrebHvQAZJbSrsV   
                          107930  spotify:track:44AH8XwgrebHvQAZJbSrsV   
                          107931  spotify:track:44AH8XwgrebHvQAZJbSrsV   

                                         Track             Artist    Album  \
Album   Artist                                                               
#1 Girl Mindless Behavior 57436     Mrs. Right  Mindless Behavior  #1 Girl   
                          159511    Mrs. Right  Mindless Behavior  #1 Girl   
                          164703    Mrs. Right  Mindless Behavior  #1 Girl   
                          220239    Mrs. Right  Mindless Behavior  #1 Girl   
                          237347    Mrs. Right  Mindless Behavior  #1 Girl   
...                                        ...                ...      ...   
÷       Ed Sheeran        808557  Shape of You         Ed Sheeran        ÷   
                          808851  Shape of You         Ed Sheeran        ÷   
スカー藩主   Scarlxrd          107907       P.T.S.D           Scarlxrd    スカー藩主   
                          107930       P.T.S.D           Scarlxrd    スカー藩主   
                          107931       P.T.S.D           Scarlxrd    スカー藩主   

                                  Date  Duration            Genre  \
Album   Artist                                                      
#1 Girl Mindless Behavior 57436    NaN    248187              RnB   
                          159511   NaN    248187              RnB   
                          164703   NaN    248187              RnB   
                          220239   NaN    248187              RnB   
                          237347   NaN    248187              RnB   
...                                ...       ...              ...   
÷       Ed Sheeran        808557   NaN    233713              Pop   
                          808851   NaN    233713              Pop   
スカー藩主   Scarlxrd          107907   NaN    307905        Dark Trap   
                          107930   NaN    307905  Underground Rap   
                          107931   NaN    307905       Trap Metal   

                                  Danceability  Energy   Key  ...  Valence  \
Album   Artist                                                ...            
#1 Girl Mindless Behavior 57436          0.439   0.753   0.0  ...    0.538   
                          159511         0.439   0.753   0.0  ...    0.538   
                          164703         0.439   0.753   0.0  ...    0.538   
                          220239         0.439   0.753   0.0  ...    0.538   
                          237347         0.439   0.753   0.0  ...    0.538   
...                                        ...     ...   ...  ...      ...   
÷       Ed Sheeran        808557         0.825   0.652   1.0  ...    0.931   
                          808851         0.825   0.652   1.0  ...    0.931   
スカー藩主   Scarlxrd          107907         0.473   0.772  10.0  ...    0.303   
                          107930         0.473   0.772  10.0  ...    0.303   
                          107931         0.473   0.772  10.0  ...    0.303   

                                    Tempo  Time Signature   Playlist  \
Album   Artist                                                         
#1 Girl Mindless Behavior 

#### Checking the before and after imputation

In [12]:
# Filter groups (albums) with at least one non-null date
valid_albums = grouped_df.filter(lambda x: x['Date'].notnull().any())

# Display the DataFrame before imputation
print("Before Imputation:")
print(valid_albums)

Before Imputation:
                                   Track URI             Track  \
0       spotify:track:6sqNctd7MlJoKDOxPVCAvU   My Happy Ending   
2       spotify:track:34ceTg8ChN5HjrqiIYCn9Q  Miss Independent   
4       spotify:track:7H6ev70Weq6DdpZyyTmUXk       Say My Name   
5       spotify:track:7H6ev70Weq6DdpZyyTmUXk       Say My Name   
7       spotify:track:4pmc2AxSEq6g7hPVlJCPyP  Jumpin', Jumpin'   
...                                      ...               ...   
809165  spotify:track:5u0YB9bpmgEPS2bPhwfRFV              arms   
809166  spotify:track:3gbBpTdY8lnQwqxNCcf795           Pompeii   
809169  spotify:track:1u0l8zWpQeMYStFkc2mLD7        Everywhere   
809171  spotify:track:64GRDrL1efgXclrhVCeuA0       Lay Me Down   
809173  spotify:track:2iUmqdfGZcHIhS3b9E9EWq   Everybody Talks   

                 Artist                      Album  Date  Duration  \
0         Avril Lavigne              Under My Skin  2004    242413   
2                 Ne-Yo      Year Of The Gentlem

In [13]:
# Define a function to impute missing dates within each group
def impute_dates(group):
    group['Date'] = group['Date'].fillna(group['Date'].max())
    return group

# Apply the impute_dates function to each group
filtered_grouped_df = valid_albums.groupby(['Album', 'Artist']).apply(impute_dates)

# Display the DataFrame after imputation
print("\nAfter Imputation:")
print(filtered_grouped_df)


After Imputation:
                                                            Track URI  \
Album   Artist                                                          
#SELFIE The Chainsmokers 11816   spotify:track:0zkiQH567SDLqfWNBaU3hv   
                         16313   spotify:track:0zkiQH567SDLqfWNBaU3hv   
                         30969   spotify:track:0zkiQH567SDLqfWNBaU3hv   
                         33911   spotify:track:0zkiQH567SDLqfWNBaU3hv   
                         40439   spotify:track:0zkiQH567SDLqfWNBaU3hv   
...                                                               ...   
xx      The xx           804446  spotify:track:0bXpmJyHHYPk6QBFj25bYF   
                         804919  spotify:track:0bXpmJyHHYPk6QBFj25bYF   
                         807013  spotify:track:0bXpmJyHHYPk6QBFj25bYF   
                         807156  spotify:track:0bXpmJyHHYPk6QBFj25bYF   
                         808215  spotify:track:0bXpmJyHHYPk6QBFj25bYF   

                               

In [17]:
df2 = filtered.copy()
# percentage of NA's
print(len(df2[df2['Date'].isna()]))
len(df2[df2['Date'].isna()]) / len(df2)

439177


0.5427459539086675

## From Artist

In [21]:
df2.reset_index(drop=True, inplace=True)
df2

Track URI         Track             Artist  \
0       spotify:track:4N4CHJqFZHyB7SBUuSFu1y    Mrs. Right  Mindless Behavior   
1       spotify:track:4N4CHJqFZHyB7SBUuSFu1y    Mrs. Right  Mindless Behavior   
2       spotify:track:4N4CHJqFZHyB7SBUuSFu1y    Mrs. Right  Mindless Behavior   
3       spotify:track:4N4CHJqFZHyB7SBUuSFu1y    Mrs. Right  Mindless Behavior   
4       spotify:track:4N4CHJqFZHyB7SBUuSFu1y    Mrs. Right  Mindless Behavior   
...                                      ...           ...                ...   
809171  spotify:track:7qiZfU4dY1lWllzX7mPBI3  Shape of You         Ed Sheeran   
809172  spotify:track:7qiZfU4dY1lWllzX7mPBI3  Shape of You         Ed Sheeran   
809173  spotify:track:44AH8XwgrebHvQAZJbSrsV       P.T.S.D           Scarlxrd   
809174  spotify:track:44AH8XwgrebHvQAZJbSrsV       P.T.S.D           Scarlxrd   
809175  spotify:track:44AH8XwgrebHvQAZJbSrsV       P.T.S.D           Scarlxrd   

          Album  Date  Duration            Genre  Danceability  Energy   Key  \
0       #1 Girl   NaN    248187              RnB         0.439   0.753   0.0   
1       #1 Girl   NaN    248187              RnB         0.439   0.753   0.0   
2       #1 Girl   NaN    248187              RnB         0.439   0.753   0.0   
3       #1 Girl   NaN    248187              RnB         0.439   0.753   0.0   
4       #1 Girl   NaN    248187              RnB         0.439   0.753   0.0   
...         ...   ...       ...              ...           ...     ...   ...   
809171        ÷   NaN    233713              Pop         0.825   0.652   1.0   
809172        ÷   NaN    233713              Pop         0.825   0.652   1.0   
809173    スカー藩主   NaN    307905        Dark Trap         0.473   0.772  10.0   
809174    スカー藩主   NaN    307905  Underground Rap         0.473   0.772  10.0   
809175    スカー藩主   NaN    307905       Trap Metal         0.473   0.772  10.0   

        ...  Valence    Tempo  Time Signature   Playlist  Num_Tracks  \
0       ...    0.538  190.678             5.0       2010          49   
1       ...    0.538  190.678             5.0   my stuff         130   
2       ...    0.538  190.678             5.0  Throwback          84   
3       ...    0.538  190.678             5.0   car jams         104   
4       ...    0.538  190.678             5.0      tunes         237   
...     ...      ...      ...             ...        ...         ...   
809171  ...    0.931  191.954             4.0         ❤️          84   
809172  ...    0.931  191.954             4.0  LET'S GO          111   
809173  ...    0.303  130.320             4.0   MAD TING          27   
809174  ...    0.303  130.320             4.0   MAD TING          27   
809175  ...    0.303  130.320             4.0   MAD TING          27   

        Num_Albums  Num_Artists  Follow  Collab     Pid  
0               39           25       1   False   11611  
1               96           72       3   False  102874  
2               74           57       1   False  103196  
3               53           35       1   False  106503  
4              127           75       1   False  107561  
...            ...          ...     ...     ...     ...  
809171          59           43       1   False  142973  
809172          59           38       1   False  142990  
809173          14           11       1   False   14661  
809174          14           11       1   False   14661  
809175          14           11       1   False   14661  

[809176 rows x 26 columns]

In [23]:
# Group by 'Artist' only
artist_group = df2.groupby('Artist')

# Filter groups (artists) with at least one non-null date
valid_artists = artist_group.filter(lambda x: x['Date'].notnull().any())

# Display the DataFrame before imputation
valid_artists.sort_values(by='Artist')

Track URI             Track     Artist  \
487810  spotify:track:4r8lRYnoOGdEi6YyI5OC1o       Bye Bye Bye     *NSYNC   
488076  spotify:track:4r8lRYnoOGdEi6YyI5OC1o       Bye Bye Bye     *NSYNC   
488077  spotify:track:4r8lRYnoOGdEi6YyI5OC1o       Bye Bye Bye     *NSYNC   
488078  spotify:track:4r8lRYnoOGdEi6YyI5OC1o       Bye Bye Bye     *NSYNC   
488079  spotify:track:35zGjsxI020C2NPKp2fzS7  It's Gonna Be Me     *NSYNC   
...                                      ...               ...        ...   
305     spotify:track:4DMPn1rEujpIJIvjy9HKV8    Scream & Shout  will.i.am   
306     spotify:track:4DMPn1rEujpIJIvjy9HKV8    Scream & Shout  will.i.am   
307     spotify:track:4DMPn1rEujpIJIvjy9HKV8    Scream & Shout  will.i.am   
297     spotify:track:4DMPn1rEujpIJIvjy9HKV8    Scream & Shout  will.i.am   
388     spotify:track:4DMPn1rEujpIJIvjy9HKV8    Scream & Shout  will.i.am   

                      Album    Date  Duration                   Genre  \
487810  No Strings Attached  2000.0    200560  boy band,dance pop,pop   
488076  No Strings Attached  2000.0    200560  boy band,dance pop,pop   
488077  No Strings Attached  2000.0    200560  boy band,dance pop,pop   
488078  No Strings Attached  2000.0    200560  boy band,dance pop,pop   
488079  No Strings Attached  2000.0    191040  boy band,dance pop,pop   
...                     ...     ...       ...                     ...   
305              #willpower     NaN    283400                     RnB   
306              #willpower     NaN    283400                     RnB   
307              #willpower     NaN    283400                     RnB   
297              #willpower     NaN    283400                     RnB   
388              #willpower     NaN    283400                     RnB   

        Danceability  Energy  Key  ...  Valence    Tempo  Time Signature  \
487810         0.614   0.928  8.0  ...    0.879  172.656             4.0   
488076         0.614   0.928  8.0  ...    0.879  172.656             4.0   
488077         0.614   0.928  8.0  ...    0.879  172.656             4.0   
488078         0.614   0.928  8.0  ...    0.879  172.656             4.0   
488079         0.644   0.874  0.0  ...    0.882  165.090             4.0   
...              ...     ...  ...  ...      ...      ...             ...   
305            0.770   0.684  0.0  ...    0.479  130.030             4.0   
306            0.770   0.684  0.0  ...    0.479  130.030             4.0   
307            0.770   0.684  0.0  ...    0.479  130.030             4.0   
297            0.770   0.684  0.0  ...    0.479  130.030             4.0   
388            0.770   0.684  0.0  ...    0.479  130.030             4.0   

            Playlist  Num_Tracks  Num_Albums  Num_Artists  Follow  Collab  \
487810          00's          44          44           41       1   False   
488076     Old Stuff         120         115          104       3   False   
488077      Stronger          44          40           31       1   False   
488078  Housewarming         134         126          117       3   False   
488079     Throwback         218         166          108       3   False   
...              ...         ...         ...          ...     ...     ...   
305          Wedding         208         181          127       1   False   
306       Party Hits         231         172          126       1   False   
307      My Music <3         106          85           62       1   False   
297          Hip hop         116         101           78       2   False   
388              Rec          17          16           15       1   False   

           Pid  
487810  100529  
488076  116786  
488077  117118  
488078  117245  
488079  117404  
...        ...  
305     113946  
306     114208  
307     114342  
297     112695  
388     131310  

[457242 rows x 26 columns]

In [24]:
valid_artists[(valid_artists['Artist'] == 'Beyoncé') & (valid_artists['Date'].isna())]

Track URI          Track   Artist  Album  \
98434  spotify:track:07lxDm1s8FVO4GF54Nooiz  Irreplaceable  Beyoncé  B'Day   
98435  spotify:track:07lxDm1s8FVO4GF54Nooiz  Irreplaceable  Beyoncé  B'Day   
98436  spotify:track:07lxDm1s8FVO4GF54Nooiz  Irreplaceable  Beyoncé  B'Day   
98437  spotify:track:07lxDm1s8FVO4GF54Nooiz  Irreplaceable  Beyoncé  B'Day   
98438  spotify:track:07lxDm1s8FVO4GF54Nooiz  Irreplaceable  Beyoncé  B'Day   
...                                     ...            ...      ...    ...   
98936  spotify:track:07lxDm1s8FVO4GF54Nooiz  Irreplaceable  Beyoncé  B'Day   
98937  spotify:track:07lxDm1s8FVO4GF54Nooiz  Irreplaceable  Beyoncé  B'Day   
98938  spotify:track:07lxDm1s8FVO4GF54Nooiz  Irreplaceable  Beyoncé  B'Day   
98939  spotify:track:07lxDm1s8FVO4GF54Nooiz  Irreplaceable  Beyoncé  B'Day   
98940  spotify:track:07lxDm1s8FVO4GF54Nooiz  Irreplaceable  Beyoncé  B'Day   

       Date  Duration Genre  Danceability  Energy   Key  ...  Valence  \
98434   NaN    227667   RnB         0.576   0.697  10.0  ...    0.501   
98435   NaN    227667   RnB         0.576   0.697  10.0  ...    0.501   
98436   NaN    227667   RnB         0.576   0.697  10.0  ...    0.501   
98437   NaN    227667   RnB         0.576   0.697  10.0  ...    0.501   
98438   NaN    227667   RnB         0.576   0.697  10.0  ...    0.501   
...     ...       ...   ...           ...     ...   ...  ...      ...   
98936   NaN    227667   RnB         0.576   0.697  10.0  ...    0.501   
98937   NaN    227667   RnB         0.576   0.697  10.0  ...    0.501   
98938   NaN    227667   RnB         0.576   0.697  10.0  ...    0.501   
98939   NaN    227667   RnB         0.576   0.697  10.0  ...    0.501   
98940   NaN    227667   RnB         0.576   0.697  10.0  ...    0.501   

         Tempo  Time Signature        Playlist  Num_Tracks  Num_Albums  \
98434  175.906             4.0          oldies          94          84   
98435  175.906             4.0           go to          99          92   
98436  175.906             4.0   motivational           41          35   
98437  175.906             4.0              🤤🤤          17          15   
98438  175.906             4.0             TBT          31          30   
...        ...             ...             ...         ...         ...   
98936  175.906             4.0  childhood jams         112          83   
98937  175.906             4.0       old skool         123         105   
98938  175.906             4.0         Beyonce          59           8   
98939  175.906             4.0             lit         133         105   
98940  175.906             4.0      APRIL 2016          35          32   

       Num_Artists  Follow  Collab     Pid  
98434           74       3   False     129  
98435           68       1   False     131  
98436           33       1   False     172  
98437            6       1   False     180  
98438           23       1   False     250  
...            ...     ...     ...     ...  
98936           62       2   False  142608  
98937           77       3   False  142774  
98938            3       1   False  142923  
98939           85       2   False  142956  
98940           30       1   False  142983  

[507 rows x 26 columns]

In [25]:
valid_artists[(valid_artists['Artist'] == 'will.i.am')]

Track URI                  Track  \
188     spotify:track:4DMPn1rEujpIJIvjy9HKV8         Scream & Shout   
189     spotify:track:4DMPn1rEujpIJIvjy9HKV8         Scream & Shout   
190     spotify:track:4DMPn1rEujpIJIvjy9HKV8         Scream & Shout   
191     spotify:track:4DMPn1rEujpIJIvjy9HKV8         Scream & Shout   
192     spotify:track:4DMPn1rEujpIJIvjy9HKV8         Scream & Shout   
...                                      ...                    ...   
583771  spotify:track:1z7FW0nlEBGtQWQ19kz7qp  I Got It From My Mama   
583772  spotify:track:1z7FW0nlEBGtQWQ19kz7qp  I Got It From My Mama   
583773  spotify:track:1z7FW0nlEBGtQWQ19kz7qp  I Got It From My Mama   
583774  spotify:track:1z7FW0nlEBGtQWQ19kz7qp  I Got It From My Mama   
583775  spotify:track:1z7FW0nlEBGtQWQ19kz7qp  I Got It From My Mama   

           Artist              Album    Date  Duration          Genre  \
188     will.i.am         #willpower     NaN    283400            RnB   
189     will.i.am         #willpower     NaN    283400            RnB   
190     will.i.am         #willpower     NaN    283400            RnB   
191     will.i.am         #willpower     NaN    283400            RnB   
192     will.i.am         #willpower     NaN    283400            RnB   
...           ...                ...     ...       ...            ...   
583771  will.i.am  Songs About Girls  2007.0    241520  dance pop,pop   
583772  will.i.am  Songs About Girls  2007.0    241520  dance pop,pop   
583773  will.i.am  Songs About Girls  2007.0    241520  dance pop,pop   
583774  will.i.am  Songs About Girls  2007.0    241520  dance pop,pop   
583775  will.i.am  Songs About Girls  2007.0    241520  dance pop,pop   

        Danceability  Energy  Key  ...  Valence    Tempo  Time Signature  \
188            0.770   0.684  0.0  ...    0.479  130.030             4.0   
189            0.770   0.684  0.0  ...    0.479  130.030             4.0   
190            0.770   0.684  0.0  ...    0.479  130.030             4.0   
191            0.770   0.684  0.0  ...    0.479  130.030             4.0   
192            0.770   0.684  0.0  ...    0.479  130.030             4.0   
...              ...     ...  ...  ...      ...      ...             ...   
583771         0.888   0.777  6.0  ...    0.876  118.998             4.0   
583772         0.888   0.777  6.0  ...    0.876  118.998             4.0   
583773         0.888   0.777  6.0  ...    0.876  118.998             4.0   
583774         0.888   0.777  6.0  ...    0.876  118.998             4.0   
583775         0.888   0.777  6.0  ...    0.876  118.998             4.0   

              Playlist  Num_Tracks  Num_Albums  Num_Artists  Follow  Collab  \
188        party music         176         156          118       2   False   
189        throw backs          70          62           45       1   False   
190         Party time          29          28           24       1   False   
191      Sweat.It.Out.          22          22           21       1    True   
192                Pop         104          97           77       1   False   
...                ...         ...         ...          ...     ...     ...   
583771         turn up         173         157          130       4   False   
583772           Anita          37          36           34       1   False   
583773            Gaby         181         137           70       3   False   
583774      APRIL 2017          28          28           25       2   False   
583775  throwback :)))         127         114           93       1   False   

           Pid  
188        124  
189        355  
190        388  
191        413  
192        729  
...        ...  
583771  120533  
583772  123490  
583773  126013  
583774  130235  
583775  136538  

[262 rows x 26 columns]

In [26]:
valid_artists[(valid_artists['Artist'] == 'Ed Sheeran') & (valid_artists['Date'].isna())]

Track URI                          Track  \
174102  spotify:track:5X6TnKT37TaSDkFm0598Uo  Castle on the Hill - Acoustic   
174103  spotify:track:5X6TnKT37TaSDkFm0598Uo  Castle on the Hill - Acoustic   
174104  spotify:track:5X6TnKT37TaSDkFm0598Uo  Castle on the Hill - Acoustic   
174105  spotify:track:5X6TnKT37TaSDkFm0598Uo  Castle on the Hill - Acoustic   
174106  spotify:track:5X6TnKT37TaSDkFm0598Uo  Castle on the Hill - Acoustic   
...                                      ...                            ...   
809168  spotify:track:0tgVpDi06FyKpA1z0VMD4v                        Perfect   
809169  spotify:track:0afhq8XCExXpqazXczTSve                    Galway Girl   
809170  spotify:track:7qiZfU4dY1lWllzX7mPBI3                   Shape of You   
809171  spotify:track:7qiZfU4dY1lWllzX7mPBI3                   Shape of You   
809172  spotify:track:7qiZfU4dY1lWllzX7mPBI3                   Shape of You   

            Artist               Album  Date  Duration Genre  Danceability  \
174102  Ed Sheeran  Castle on the Hill   NaN    226227   Emo         0.563   
174103  Ed Sheeran  Castle on the Hill   NaN    226227   Emo         0.563   
174104  Ed Sheeran  Castle on the Hill   NaN    226227   Emo         0.563   
174105  Ed Sheeran  Castle on the Hill   NaN    226227   Emo         0.563   
174106  Ed Sheeran  Castle on the Hill   NaN    226227   Emo         0.563   
...            ...                 ...   ...       ...   ...           ...   
809168  Ed Sheeran                   ÷   NaN    263400   Pop         0.599   
809169  Ed Sheeran                   ÷   NaN    170827   Pop         0.624   
809170  Ed Sheeran                   ÷   NaN    233713   Pop         0.825   
809171  Ed Sheeran                   ÷   NaN    233713   Pop         0.825   
809172  Ed Sheeran                   ÷   NaN    233713   Pop         0.825   

        Energy  Key  ...  Valence    Tempo  Time Signature         Playlist  \
174102   0.260  2.0  ...    0.616  145.561             4.0   Acoustic songs   
174103   0.260  2.0  ...    0.616  145.561             4.0     Acoustic Pop   
174104   0.260  2.0  ...    0.616  145.561             4.0      chill vibes   
174105   0.260  2.0  ...    0.616  145.561             4.0             NEW    
174106   0.260  2.0  ...    0.616  145.561             4.0            Happy   
...        ...  ...  ...      ...      ...             ...              ...   
809168   0.448  8.0  ...    0.168  190.100             3.0              lit   
809169   0.876  9.0  ...    0.781  199.886             4.0           Sydney   
809170   0.652  1.0  ...    0.931  191.954             4.0               ❤️   
809171   0.652  1.0  ...    0.931  191.954             4.0               ❤️   
809172   0.652  1.0  ...    0.931  191.954             4.0        LET'S GO    

        Num_Tracks  Num_Albums  Num_Artists  Follow  Collab     Pid  
174102          32          32           29       1   False   10104  
174103         134         130          106       2   False   11323  
174104          36          32           27       1   False   13239  
174105          42          42           37       1   False   13327  
174106         200         141           95       1   False   13769  
...            ...         ...          ...     ...     ...     ...  
809168         133         105           85       2   False  142956  
809169         118         102           86       1   False  142964  
809170          84          59           43       1   False  142973  
809171          84          59           43       1   False  142973  
809172         111          59           38       1   False  142990  

[3966 rows x 26 columns]

In [27]:
valid_artists[(valid_artists['Artist'] == '112')]

Track URI  \
8672    spotify:track:3kVIFDE3G89I2RPVkiRaRj   
8673    spotify:track:3kVIFDE3G89I2RPVkiRaRj   
8674    spotify:track:3kVIFDE3G89I2RPVkiRaRj   
8675    spotify:track:3kVIFDE3G89I2RPVkiRaRj   
8676    spotify:track:3kVIFDE3G89I2RPVkiRaRj   
...                                      ...   
538215  spotify:track:6iajHa34cSiD5s42Cq9miJ   
538216  spotify:track:6iajHa34cSiD5s42Cq9miJ   
538217  spotify:track:6iajHa34cSiD5s42Cq9miJ   
538218  spotify:track:6iajHa34cSiD5s42Cq9miJ   
538219  spotify:track:6iajHa34cSiD5s42Cq9miJ   

                                   Track Artist     Album  Date  Duration  \
8672                               Cupid    112       112   NaN    252267   
8673                               Cupid    112       112   NaN    252267   
8674                               Cupid    112       112   NaN    252267   
8675                               Cupid    112       112   NaN    252267   
8676                               Cupid    112       112   NaN    252267   
...                                  ...    ...       ...   ...       ...   
538215  Peaches & Cream (feat. P. Diddy)    112  R&B Hits   NaN    225947   
538216  Peaches & Cream (feat. P. Diddy)    112  R&B Hits   NaN    225947   
538217  Peaches & Cream (feat. P. Diddy)    112  R&B Hits   NaN    225947   
538218  Peaches & Cream (feat. P. Diddy)    112  R&B Hits   NaN    225947   
538219  Peaches & Cream (feat. P. Diddy)    112  R&B Hits   NaN    225947   

         Genre  Danceability  Energy  Key  ...  Valence    Tempo  \
8672       RnB         0.685   0.380  8.0  ...    0.870  175.562   
8673       RnB         0.685   0.380  8.0  ...    0.870  175.562   
8674       RnB         0.685   0.380  8.0  ...    0.870  175.562   
8675       RnB         0.685   0.380  8.0  ...    0.870  175.562   
8676       RnB         0.685   0.380  8.0  ...    0.870  175.562   
...        ...           ...     ...  ...  ...      ...      ...   
538215  Hiphop         0.706   0.537  7.0  ...    0.775  203.746   
538216  Hiphop         0.706   0.537  7.0  ...    0.775  203.746   
538217  Hiphop         0.706   0.537  7.0  ...    0.775  203.746   
538218  Hiphop         0.706   0.537  7.0  ...    0.775  203.746   
538219  Hiphop         0.706   0.537  7.0  ...    0.775  203.746   

        Time Signature       Playlist  Num_Tracks  Num_Albums  Num_Artists  \
8672               4.0     Love Music         188         157          103   
8673               4.0      Seduction         120          97           63   
8674               4.0          David          33          31           26   
8675               4.0  R&B classics          110          89           69   
8676               4.0  R&B classics          110          89           69   
...                ...            ...         ...         ...          ...   
538215             4.0        workout          87          80           72   
538216             4.0             ee          97          91           79   
538217             4.0       R&B Jams         171         139          103   
538218             4.0      san Diego          77          64           51   
538219             4.0       Football          68          66           61   

        Follow  Collab     Pid  
8672         2   False     156  
8673         1   False     930  
8674         1    True     989  
8675         1   False    1104  
8676         1   False    1104  
...        ...     ...     ...  
538215       1   False  139415  
538216       1   False  139887  
538217       1   False  141313  
538218       4   False  141406  
538219       2   False  141981  

[315 rows x 26 columns]

In [28]:
# Define a function to impute missing dates within each group
def impute_dates(group):
    group['Date'] = group['Date'].fillna(group['Date'].mean())
    return group

# Apply the impute_dates function to each group
filtered2 = artist_group.apply(impute_dates)
filtered2

Track URI  \
Artist                                                     
$hun        699846  spotify:track:3NRgC9yCkATmwnhMo1dZI7   
$uicideBoy$ 482     spotify:track:6lrOr4Ks7b6B03n0YmKjND   
            483     spotify:track:6lrOr4Ks7b6B03n0YmKjND   
            484     spotify:track:6lrOr4Ks7b6B03n0YmKjND   
            485     spotify:track:6lrOr4Ks7b6B03n0YmKjND   
...                                                  ...   
xxyyxx      782409  spotify:track:6TMSo0TqIKaotFuWeUKxc6   
            782410  spotify:track:6TMSo0TqIKaotFuWeUKxc6   
            782411  spotify:track:6TMSo0TqIKaotFuWeUKxc6   
            782412  spotify:track:6TMSo0TqIKaotFuWeUKxc6   
∆aimon      72041   spotify:track:200NBSoWbdGVyucC1yjBE2   

                                          Track       Artist  \
Artist                                                         
$hun        699846  Nikes on My Feet (Extended)         $hun   
$uicideBoy$ 482                     Cold Turkey  $uicideBoy$   
            483                     Cold Turkey  $uicideBoy$   
            484                     Cold Turkey  $uicideBoy$   
            485                     Cold Turkey  $uicideBoy$   
...                                         ...          ...   
xxyyxx      782409                          Dmt       xxyyxx   
            782410                          Dmt       xxyyxx   
            782411                          Dmt       xxyyxx   
            782412                          Dmt       xxyyxx   
∆aimon      72041                          Amen       ∆aimon   

                                 Album  Date  Duration            Genre  \
Artist                                                                    
$hun        699846     The Rough Draft   NaN    328411  Underground Rap   
$uicideBoy$ 482     $outh $ide $uicide   NaN    182334       Trap Metal   
            483     $outh $ide $uicide   NaN    182334  Underground Rap   
            484     $outh $ide $uicide   NaN    182334        Dark Trap   
            485     $outh $ide $uicide   NaN    182334       Trap Metal   
...                                ...   ...       ...              ...   
xxyyxx      782409              Xxyyxx   NaN    260206        Dark Trap   
            782410              Xxyyxx   NaN    260206        Dark Trap   
            782411              Xxyyxx   NaN    260206        Dark Trap   
            782412              Xxyyxx   NaN    260206        Dark Trap   
∆aimon      72041                 Amen   NaN    256173        Dark Trap   

                    Danceability  Energy   Key  ...  Valence    Tempo  \
Artist                                          ...                     
$hun        699846         0.808   0.488   9.0  ...   0.4820  184.142   
$uicideBoy$ 482            0.891   0.670   1.0  ...   0.1800  212.032   
            483            0.891   0.670   1.0  ...   0.1800  106.016   
            484            0.891   0.670   1.0  ...   0.1800  212.032   
            485            0.891   0.670   1.0  ...   0.1800  212.032   
...                          ...     ...   ...  ...      ...      ...   
xxyyxx      782409         0.537   0.424   1.0  ...   0.0761  193.994   
            782410         0.537   0.424   1.0  ...   0.0761  193.994   
            782411         0.537   0.424   1.0  ...   0.0761  193.994   
            782412         0.537   0.424   1.0  ...   0.0761  193.994   
∆aimon      72041          0.701   0.558  11.0  ...   0.1290  190.012   

                    Time Signature     Playlist  Num_Tracks  Num_Albums  \
Artist                                                                    
$hun        699846             4.0       Wavy ~         130          78   
$uicideBoy$ 482                4.0       Adrian         118          81   
            483                4.0       Adrian         118          81   
            484                4.0       Adrian         118          81   
            485                4.0      new new         1

In [29]:
filtered2[filtered2['Track']=='Irreplaceable']

Track URI          Track   Artist  \
Artist                                                                        
Beyoncé 98434  spotify:track:07lxDm1s8FVO4GF54Nooiz  Irreplaceable  Beyoncé   
        98435  spotify:track:07lxDm1s8FVO4GF54Nooiz  Irreplaceable  Beyoncé   
        98436  spotify:track:07lxDm1s8FVO4GF54Nooiz  Irreplaceable  Beyoncé   
        98437  spotify:track:07lxDm1s8FVO4GF54Nooiz  Irreplaceable  Beyoncé   
        98438  spotify:track:07lxDm1s8FVO4GF54Nooiz  Irreplaceable  Beyoncé   
...                                             ...            ...      ...   
        98936  spotify:track:07lxDm1s8FVO4GF54Nooiz  Irreplaceable  Beyoncé   
        98937  spotify:track:07lxDm1s8FVO4GF54Nooiz  Irreplaceable  Beyoncé   
        98938  spotify:track:07lxDm1s8FVO4GF54Nooiz  Irreplaceable  Beyoncé   
        98939  spotify:track:07lxDm1s8FVO4GF54Nooiz  Irreplaceable  Beyoncé   
        98940  spotify:track:07lxDm1s8FVO4GF54Nooiz  Irreplaceable  Beyoncé   

               Album         Date  Duration Genre  Danceability  Energy   Key  \
Artist                                                                          
Beyoncé 98434  B'Day  2009.832061    227667   RnB         0.576   0.697  10.0   
        98435  B'Day  2009.832061    227667   RnB         0.576   0.697  10.0   
        98436  B'Day  2009.832061    227667   RnB         0.576   0.697  10.0   
        98437  B'Day  2009.832061    227667   RnB         0.576   0.697  10.0   
        98438  B'Day  2009.832061    227667   RnB         0.576   0.697  10.0   
...              ...          ...       ...   ...           ...     ...   ...   
        98936  B'Day  2009.832061    227667   RnB         0.576   0.697  10.0   
        98937  B'Day  2009.832061    227667   RnB         0.576   0.697  10.0   
        98938  B'Day  2009.832061    227667   RnB         0.576   0.697  10.0   
        98939  B'Day  2009.832061    227667   RnB         0.576   0.697  10.0   
        98940  B'Day  2009.832061    227667   RnB         0.576   0.697  10.0   

               ...  Valence    Tempo  Time Signature        Playlist  \
Artist         ...                                                     
Beyoncé 98434  ...    0.501  175.906             4.0          oldies   
        98435  ...    0.501  175.906             4.0           go to   
        98436  ...    0.501  175.906             4.0   motivational    
        98437  ...    0.501  175.906             4.0              🤤🤤   
        98438  ...    0.501  175.906             4.0             TBT   
...            ...      ...      ...             ...             ...   
        98936  ...    0.501  175.906             4.0  childhood jams   
        98937  ...    0.501  175.906             4.0       old skool   
        98938  ...    0.501  175.906             4.0         Beyonce   
        98939  ...    0.501  175.906             4.0             lit   
        98940  ...    0.501  175.906             4.0      APRIL 2016   

               Num_Tracks  Num_Albums  Num_Artists  Follow  Collab     Pid  
Artist                                                                      
Beyoncé 98434          94          84           74       3   False     129  
        98435          99          92           68       1   False     131  
        98436          41          35           33       1   False     172  
        98437          17          15            6       1   False     180  
        98438          31          30           23       1   False     250  
...                   ...         ...          ...     ...     ...     ...  
        98936         112          83           62       2   False  142608  
        98937         123         105           77       3   False  142774  
        98938          59           8            3       1   False  142923  
        98939         133         105           85       2   False  142956  
        98940          35          32           30       1   False  142983  

[507 rows x 26 column

In [30]:
filtered2[(filtered2['Artist'] == 'will.i.am')]

Track URI                  Track  \
Artist                                                                          
will.i.am 188     spotify:track:4DMPn1rEujpIJIvjy9HKV8         Scream & Shout   
          189     spotify:track:4DMPn1rEujpIJIvjy9HKV8         Scream & Shout   
          190     spotify:track:4DMPn1rEujpIJIvjy9HKV8         Scream & Shout   
          191     spotify:track:4DMPn1rEujpIJIvjy9HKV8         Scream & Shout   
          192     spotify:track:4DMPn1rEujpIJIvjy9HKV8         Scream & Shout   
...                                                ...                    ...   
          583771  spotify:track:1z7FW0nlEBGtQWQ19kz7qp  I Got It From My Mama   
          583772  spotify:track:1z7FW0nlEBGtQWQ19kz7qp  I Got It From My Mama   
          583773  spotify:track:1z7FW0nlEBGtQWQ19kz7qp  I Got It From My Mama   
          583774  spotify:track:1z7FW0nlEBGtQWQ19kz7qp  I Got It From My Mama   
          583775  spotify:track:1z7FW0nlEBGtQWQ19kz7qp  I Got It From My Mama   

                     Artist              Album    Date  Duration  \
Artist                                                             
will.i.am 188     will.i.am         #willpower  2007.0    283400   
          189     will.i.am         #willpower  2007.0    283400   
          190     will.i.am         #willpower  2007.0    283400   
          191     will.i.am         #willpower  2007.0    283400   
          192     will.i.am         #willpower  2007.0    283400   
...                     ...                ...     ...       ...   
          583771  will.i.am  Songs About Girls  2007.0    241520   
          583772  will.i.am  Songs About Girls  2007.0    241520   
          583773  will.i.am  Songs About Girls  2007.0    241520   
          583774  will.i.am  Songs About Girls  2007.0    241520   
          583775  will.i.am  Songs About Girls  2007.0    241520   

                          Genre  Danceability  Energy  Key  ...  Valence  \
Artist                                                      ...            
will.i.am 188               RnB         0.770   0.684  0.0  ...    0.479   
          189               RnB         0.770   0.684  0.0  ...    0.479   
          190               RnB         0.770   0.684  0.0  ...    0.479   
          191               RnB         0.770   0.684  0.0  ...    0.479   
          192               RnB         0.770   0.684  0.0  ...    0.479   
...                         ...           ...     ...  ...  ...      ...   
          583771  dance pop,pop         0.888   0.777  6.0  ...    0.876   
          583772  dance pop,pop         0.888   0.777  6.0  ...    0.876   
          583773  dance pop,pop         0.888   0.777  6.0  ...    0.876   
          583774  dance pop,pop         0.888   0.777  6.0  ...    0.876   
          583775  dance pop,pop         0.888   0.777  6.0  ...    0.876   

                    Tempo  Time Signature        Playlist  Num_Tracks  \
Artist                                                                  
will.i.am 188     130.030             4.0     party music         176   
          189     130.030             4.0     throw backs          70   
          190     130.030             4.0      Party time          29   
          191     130.030             4.0   Sweat.It.Out.          22   
          192     130.030             4.0             Pop         104   
...                   ...             ...             ...         ...   
          583771  118.998             4.0         turn up         173   
          583772  118.998             4.0           Anita          37   
          583773  118.998             4.0            Gaby         181   
          583774  118.998             4.0      APRIL 2017          28   
          583775  118.998             4.0  throwback :)))         127   

                  Num_Albums  Num_Artists  Follow  Collab     Pid  
Artist                                                             
will.i.am 188            156   

In [31]:
filtered2[(filtered2['Artist'] == 'Ed Sheeran')]

Track URI         Track  \
Artist                                                                  
Ed Sheeran 2103    spotify:track:53Pgsvu3qSYO2aXt5J2vcL    Lego House   
           2104    spotify:track:53Pgsvu3qSYO2aXt5J2vcL    Lego House   
           2105    spotify:track:1VdZ0vKfR5jneCmWIUAMxK    The A Team   
           2106    spotify:track:1VdZ0vKfR5jneCmWIUAMxK    The A Team   
           2107    spotify:track:1VdZ0vKfR5jneCmWIUAMxK    The A Team   
...                                                 ...           ...   
           809168  spotify:track:0tgVpDi06FyKpA1z0VMD4v       Perfect   
           809169  spotify:track:0afhq8XCExXpqazXczTSve   Galway Girl   
           809170  spotify:track:7qiZfU4dY1lWllzX7mPBI3  Shape of You   
           809171  spotify:track:7qiZfU4dY1lWllzX7mPBI3  Shape of You   
           809172  spotify:track:7qiZfU4dY1lWllzX7mPBI3  Shape of You   

                       Artist Album         Date  Duration  \
Artist                                                       
Ed Sheeran 2103    Ed Sheeran     +  2011.000000    185093   
           2104    Ed Sheeran     +  2011.000000    185093   
           2105    Ed Sheeran     +  2011.000000    258373   
           2106    Ed Sheeran     +  2011.000000    258373   
           2107    Ed Sheeran     +  2011.000000    258373   
...                       ...   ...          ...       ...   
           809168  Ed Sheeran     ÷  2011.034059    263400   
           809169  Ed Sheeran     ÷  2011.034059    170827   
           809170  Ed Sheeran     ÷  2011.034059    233713   
           809171  Ed Sheeran     ÷  2011.034059    233713   
           809172  Ed Sheeran     ÷  2011.034059    233713   

                                              Genre  Danceability  Energy  \
Artist                                                                      
Ed Sheeran 2103    pop,singer-songwriter pop,uk pop         0.592   0.637   
           2104    pop,singer-songwriter pop,uk pop         0.592   0.637   
           2105                                 Emo         0.642   0.289   
           2106    pop,singer-songwriter pop,uk pop         0.642   0.289   
           2107    pop,singer-songwriter pop,uk pop         0.642   0.289   
...                                             ...           ...     ...   
           809168                               Pop         0.599   0.448   
           809169                               Pop         0.624   0.876   
           809170                               Pop         0.825   0.652   
           809171                               Pop         0.825   0.652   
           809172                               Pop         0.825   0.652   

                    Key  ...  Valence    Tempo  Time Signature  \
Artist                   ...                                     
Ed Sheeran 2103    11.0  ...    0.565  159.701             4.0   
           2104    11.0  ...    0.565  159.701             4.0   
           2105     9.0  ...    0.407  169.992             4.0   
           2106     9.0  ...    0.407   84.996             4.0   
           2107     9.0  ...    0.407   84.996             4.0   
...                 ...  ...      ...      ...             ...   
           809168   8.0  ...    0.168  190.100             3.0   
           809169   9.0  ...    0.781  199.886             4.0   
           809170   1.0  ...    0.931  191.954             4.0   
           809171   1.0  ...    0.931  191.954             4.0   
           809172   1.0  ...    0.931  191.954             4.0   

                         Playlist  Num_Tracks  Num_Albums  Num_Artists  \
Artist                                                                   
Ed Sheeran 2103    Mom's playlist          79          69           61   
           2104     Road Trippin'         158         131          106   
           2105             Chill          66          54           30   
           2106             Chill          66          54 

In [32]:
filtered2[(filtered2['Artist'] == '112')]

Track URI  \
Artist                                                
112    8672    spotify:track:3kVIFDE3G89I2RPVkiRaRj   
       8673    spotify:track:3kVIFDE3G89I2RPVkiRaRj   
       8674    spotify:track:3kVIFDE3G89I2RPVkiRaRj   
       8675    spotify:track:3kVIFDE3G89I2RPVkiRaRj   
       8676    spotify:track:3kVIFDE3G89I2RPVkiRaRj   
...                                             ...   
       538215  spotify:track:6iajHa34cSiD5s42Cq9miJ   
       538216  spotify:track:6iajHa34cSiD5s42Cq9miJ   
       538217  spotify:track:6iajHa34cSiD5s42Cq9miJ   
       538218  spotify:track:6iajHa34cSiD5s42Cq9miJ   
       538219  spotify:track:6iajHa34cSiD5s42Cq9miJ   

                                          Track Artist     Album    Date  \
Artist                                                                     
112    8672                               Cupid    112       112  2001.0   
       8673                               Cupid    112       112  2001.0   
       8674                               Cupid    112       112  2001.0   
       8675                               Cupid    112       112  2001.0   
       8676                               Cupid    112       112  2001.0   
...                                         ...    ...       ...     ...   
       538215  Peaches & Cream (feat. P. Diddy)    112  R&B Hits  2001.0   
       538216  Peaches & Cream (feat. P. Diddy)    112  R&B Hits  2001.0   
       538217  Peaches & Cream (feat. P. Diddy)    112  R&B Hits  2001.0   
       538218  Peaches & Cream (feat. P. Diddy)    112  R&B Hits  2001.0   
       538219  Peaches & Cream (feat. P. Diddy)    112  R&B Hits  2001.0   

               Duration   Genre  Danceability  Energy  Key  ...  Valence  \
Artist                                                      ...            
112    8672      252267     RnB         0.685   0.380  8.0  ...    0.870   
       8673      252267     RnB         0.685   0.380  8.0  ...    0.870   
       8674      252267     RnB         0.685   0.380  8.0  ...    0.870   
       8675      252267     RnB         0.685   0.380  8.0  ...    0.870   
       8676      252267     RnB         0.685   0.380  8.0  ...    0.870   
...                 ...     ...           ...     ...  ...  ...      ...   
       538215    225947  Hiphop         0.706   0.537  7.0  ...    0.775   
       538216    225947  Hiphop         0.706   0.537  7.0  ...    0.775   
       538217    225947  Hiphop         0.706   0.537  7.0  ...    0.775   
       538218    225947  Hiphop         0.706   0.537  7.0  ...    0.775   
       538219    225947  Hiphop         0.706   0.537  7.0  ...    0.775   

                 Tempo  Time Signature       Playlist  Num_Tracks  Num_Albums  \
Artist                                                                          
112    8672    175.562             4.0     Love Music         188         157   
       8673    175.562             4.0      Seduction         120          97   
       8674    175.562             4.0          David          33          31   
       8675    175.562             4.0  R&B classics          110          89   
       8676    175.562             4.0  R&B classics          110          89   
...                ...             ...            ...         ...         ...   
       538215  203.746             4.0        workout          87          80   
       538216  203.746             4.0             ee          97          91   
       538217  203.746             4.0       R&B Jams         171         139   
       538218  203.746             4.0      san Diego          77          64   
       538219  203.746             4.0       Football          68          66   

               Num_Artists  Follow  Collab     Pid  
Artist                                              
112    8672            103       2   False     156  
       8673             63       1   False     930  
       8674             26       1    True     989  
       8675             69   

Here, we see that Beyoncé's song 'Irreplaceable' had the date imputed as 2010, when the actual date is 2006. For 'Scream and Shout', the imputed date is 2007 when the actual date is 2013. These aren't too far. 

For Ed Sheeran all songs have been imputed to 2011. The actual dates are: 'Shape of you': 2017; 'Photograph': 2014; 'Galway girl': 2017; 'Castle on the Hill': 2017; 'Perfect': 2017. 

The dates of songs from 112 have all been imputed to 2001. The actual dates are 2001, 1996, 2005, 2005.

All of those have less than a 10 year difference. So we can assume that our imputation based on artists is valid.

In [33]:
df3 = filtered2.copy()
# percentage of NA's
print(len(df3[df3['Date'].isna()]))
len(df3[df3['Date'].isna()]) / len(df3)

351934


0.43492886590803487

## From Pid

In [34]:
df3[df3['Date'].isna()]

Track URI  \
Artist                                                     
$hun        699846  spotify:track:3NRgC9yCkATmwnhMo1dZI7   
$uicideBoy$ 482     spotify:track:6lrOr4Ks7b6B03n0YmKjND   
            483     spotify:track:6lrOr4Ks7b6B03n0YmKjND   
            484     spotify:track:6lrOr4Ks7b6B03n0YmKjND   
            485     spotify:track:6lrOr4Ks7b6B03n0YmKjND   
...                                                  ...   
xxyyxx      782409  spotify:track:6TMSo0TqIKaotFuWeUKxc6   
            782410  spotify:track:6TMSo0TqIKaotFuWeUKxc6   
            782411  spotify:track:6TMSo0TqIKaotFuWeUKxc6   
            782412  spotify:track:6TMSo0TqIKaotFuWeUKxc6   
∆aimon      72041   spotify:track:200NBSoWbdGVyucC1yjBE2   

                                          Track       Artist  \
Artist                                                         
$hun        699846  Nikes on My Feet (Extended)         $hun   
$uicideBoy$ 482                     Cold Turkey  $uicideBoy$   
            483                     Cold Turkey  $uicideBoy$   
            484                     Cold Turkey  $uicideBoy$   
            485                     Cold Turkey  $uicideBoy$   
...                                         ...          ...   
xxyyxx      782409                          Dmt       xxyyxx   
            782410                          Dmt       xxyyxx   
            782411                          Dmt       xxyyxx   
            782412                          Dmt       xxyyxx   
∆aimon      72041                          Amen       ∆aimon   

                                 Album  Date  Duration            Genre  \
Artist                                                                    
$hun        699846     The Rough Draft   NaN    328411  Underground Rap   
$uicideBoy$ 482     $outh $ide $uicide   NaN    182334       Trap Metal   
            483     $outh $ide $uicide   NaN    182334  Underground Rap   
            484     $outh $ide $uicide   NaN    182334        Dark Trap   
            485     $outh $ide $uicide   NaN    182334       Trap Metal   
...                                ...   ...       ...              ...   
xxyyxx      782409              Xxyyxx   NaN    260206        Dark Trap   
            782410              Xxyyxx   NaN    260206        Dark Trap   
            782411              Xxyyxx   NaN    260206        Dark Trap   
            782412              Xxyyxx   NaN    260206        Dark Trap   
∆aimon      72041                 Amen   NaN    256173        Dark Trap   

                    Danceability  Energy   Key  ...  Valence    Tempo  \
Artist                                          ...                     
$hun        699846         0.808   0.488   9.0  ...   0.4820  184.142   
$uicideBoy$ 482            0.891   0.670   1.0  ...   0.1800  212.032   
            483            0.891   0.670   1.0  ...   0.1800  106.016   
            484            0.891   0.670   1.0  ...   0.1800  212.032   
            485            0.891   0.670   1.0  ...   0.1800  212.032   
...                          ...     ...   ...  ...      ...      ...   
xxyyxx      782409         0.537   0.424   1.0  ...   0.0761  193.994   
            782410         0.537   0.424   1.0  ...   0.0761  193.994   
            782411         0.537   0.424   1.0  ...   0.0761  193.994   
            782412         0.537   0.424   1.0  ...   0.0761  193.994   
∆aimon      72041          0.701   0.558  11.0  ...   0.1290  190.012   

                    Time Signature     Playlist  Num_Tracks  Num_Albums  \
Artist                                                                    
$hun        699846             4.0       Wavy ~         130          78   
$uicideBoy$ 482                4.0       Adrian         118          81   
            483                4.0       Adrian         118          81   
            484                4.0       Adrian         118          81   
            485                4.0      new new         1

In [36]:
df4 = df3.copy()
# Group by the 'Pid' column and calculate the mean date for each playlist
missing_dates = df3['Date'].isna()
playlist_mean_dates = df3.groupby('Pid')['Date'].transform('mean')
# Impute missing values in the 'Date' column with the mean date of the corresponding playlist
df4.loc[missing_dates, 'Date'] = playlist_mean_dates[missing_dates]
# Check if there are non-numeric values in the 'Date' column
non_numeric_dates = pd.to_numeric(df4['Date'], errors='coerce').isna()
# If there are non-numeric values, handle or remove them
# For example, you can replace non-numeric values with NaN
df4.loc[non_numeric_dates, 'Date'] = pd.to_numeric(df4.loc[non_numeric_dates, 'Date'], errors='coerce')
# Impute NaN values with the mean (you can choose a different imputation strategy)
df4['Date'].fillna(df4['Date'].mean(), inplace=True)
# Convert the 'Date' column to int type
df4['Date'] = df4['Date'].astype(int)
df4.iloc[df3[df3['Date'].isna()].index]

In [37]:
df4[df4['Track']=="Leavin'"]

Track URI    Track  \
Artist                                                                  
Jesse McCartney 235669  spotify:track:20ORwCJusz4KS2PbTPVNKo  Leavin'   
                235670  spotify:track:20ORwCJusz4KS2PbTPVNKo  Leavin'   
                235671  spotify:track:20ORwCJusz4KS2PbTPVNKo  Leavin'   
                235672  spotify:track:20ORwCJusz4KS2PbTPVNKo  Leavin'   
                235673  spotify:track:20ORwCJusz4KS2PbTPVNKo  Leavin'   
...                                                      ...      ...   
                235930  spotify:track:20ORwCJusz4KS2PbTPVNKo  Leavin'   
                235931  spotify:track:20ORwCJusz4KS2PbTPVNKo  Leavin'   
                235932  spotify:track:20ORwCJusz4KS2PbTPVNKo  Leavin'   
                235933  spotify:track:20ORwCJusz4KS2PbTPVNKo  Leavin'   
                235934  spotify:track:20ORwCJusz4KS2PbTPVNKo  Leavin'   

                                 Artist                  Album  Date  \
Artist                                                                 
Jesse McCartney 235669  Jesse McCartney  Departure - Recharged  2003   
                235670  Jesse McCartney  Departure - Recharged  2005   
                235671  Jesse McCartney  Departure - Recharged  2006   
                235672  Jesse McCartney  Departure - Recharged  2005   
                235673  Jesse McCartney  Departure - Recharged  2004   
...                                 ...                    ...   ...   
                235930  Jesse McCartney  Departure - Recharged  2013   
                235931  Jesse McCartney  Departure - Recharged  2006   
                235932  Jesse McCartney  Departure - Recharged  2008   
                235933  Jesse McCartney  Departure - Recharged  2001   
                235934  Jesse McCartney  Departure - Recharged  2009   

                        Duration Genre  Danceability  Energy  Key  ...  \
Artist                                                             ...   
Jesse McCartney 235669    216880   RnB         0.687    0.71  9.0  ...   
                235670    216880   RnB         0.687    0.71  9.0  ...   
                235671    216880   RnB         0.687    0.71  9.0  ...   
                235672    216880   RnB         0.687    0.71  9.0  ...   
                235673    216880   RnB         0.687    0.71  9.0  ...   
...                          ...   ...           ...     ...  ...  ...   
                235930    216880   RnB         0.687    0.71  9.0  ...   
                235931    216880   RnB         0.687    0.71  9.0  ...   
                235932    216880   RnB         0.687    0.71  9.0  ...   
                235933    216880   RnB         0.687    0.71  9.0  ...   
                235934    216880   RnB         0.687    0.71  9.0  ...   

                        Valence   Tempo  Time Signature    Playlist  \
Artist                                                                
Jesse McCartney 235669    0.886  158.47             4.0  Throwbacks   
                235670    0.886  158.47             4.0       Feels   
                235671    0.886  158.47             4.0  Throwbacks   
                235672    0.886  158.47             4.0       2000s   
                235673    0.886  158.47             4.0      oldies   
...                         ...     ...             ...         ...   
                235930    0.886  158.47             4.0        Best   
                235931    0.886  158.47             4.0   Road Trip   
                235932    0.886  158.47             4.0          tb   
                235933    0.886  158.47             4.0     Randoms   
                235934    0.886  158.47             4.0      Oldies   

                        Num_Tracks  Num_Albums  Num_Artists  Follow  Collab  \
Artist                                                                        
Jesse McCartney 235669          52          47           37       1   False   
                235670          94      

Now, notice that each song is repeated several times (here Leavin' is repeated 266 times) because they appear in different playlists. We can take the mean value for the dates that were imputed for each song for each playlist.

In [38]:
df4.groupby(['Track', 'Artist'], as_index = False).filter(lambda x: len(x) == 1)

ValueError: 'Artist' is both an index level and a column label, which is ambiguous.

In [ ]:
df_mean_date = df4.groupby(['Track URI'])['Date'].mean().reset_index()
df_mean_date

Track URI         Date
0     spotify:track:00Dj0k3r0a6HKTLanwET8L  2009.000000
1     spotify:track:00FROhC5g4iJdax5US8jRr  2000.461538
2     spotify:track:00LfFm08VWeZwB0Zlm24AT  2005.771791
3     spotify:track:00MI0oGDVJYM1qWbyUOIhH  2008.000000
4     spotify:track:00tB8c71eTcG5jV7PhuF4Q  2002.000000
...                                    ...          ...
4826  spotify:track:7zFXmv6vqI4qOt4yGf3jYZ  2012.088415
4827  spotify:track:7zP67rufQgoODWFI45jntD  2008.000000
4828  spotify:track:7zQ5nqAKKfk0gtBgV70gyq  2004.000000
4829  spotify:track:7zez4ZwqfSqD6fPQgcnqwu  2013.000000
4830  spotify:track:7zrWPRYubwn8k8Id80LDCv  1997.000000

[4831 rows x 2 columns]

In [ ]:
df4

Track URI             Track  \
0       spotify:track:6sqNctd7MlJoKDOxPVCAvU   My Happy Ending   
1       spotify:track:3BxWKCI06eQ5Od8TY2JBeA           Buttons   
2       spotify:track:34ceTg8ChN5HjrqiIYCn9Q  Miss Independent   
3       spotify:track:67T6l4q3zVjC5nZZPXByU8       Whatcha Say   
4       spotify:track:7H6ev70Weq6DdpZyyTmUXk       Say My Name   
...                                      ...               ...   
809171  spotify:track:64GRDrL1efgXclrhVCeuA0       Lay Me Down   
809172  spotify:track:4kdfjhj9xNkYU0R8xlDy8k             6 Man   
809173  spotify:track:2iUmqdfGZcHIhS3b9E9EWq   Everybody Talks   
809174  spotify:track:5InOp6q2vvx0fShv3bzFLZ     Know Yourself   
809175  spotify:track:7JXZq0JgG2zTrSOAgY8VMC            Jungle   

                    Artist                                 Album  Date  \
0            Avril Lavigne                         Under My Skin  2004   
1       The Pussycat Dolls                                   PCD  2008   
2                    Ne-Yo                 Year Of The Gentleman  2008   
3             Jason Derulo                          Jason Derulo  2013   
4          Destiny's Child             The Writing's On The Wall  1999   
...                    ...                                   ...   ...   
809171           Sam Smith                    In The Lonely Hour  2014   
809172               Drake  If You're Reading This It's Too Late  2016   
809173          Neon Trees                          Picture Show  2012   
809174               Drake  If You're Reading This It's Too Late  2016   
809175               Drake  If You're Reading This It's Too Late  2016   

        Duration                                       Genre  Danceability  \
0         242413                  canadian pop,candy pop,pop         0.414   
1         225560                                         RnB         0.570   
2         232000                                         RnB         0.673   
3         221253                                         RnB         0.615   
4         271333                                         RnB         0.713   
...          ...                                         ...           ...   
809171    219536                                         Emo         0.468   
809172    167653                                      Hiphop         0.568   
809173    177280  modern rock,neo mellow,pop rock,pov: indie         0.471   
809174    275840                                         Rap         0.720   
809175    320400                                         RnB         0.697   

        Energy   Key  ...  Valence    Tempo  Time Signature    Playlist  \
0        0.936   2.0  ...    0.740  170.229             4.0  Throwbacks   
1        0.821   2.0  ...    0.408  210.857             4.0  Throwbacks   
2        0.683   1.0  ...    0.713  171.860             4.0  Throwbacks   
3        0.711  11.0  ...    0.711  144.036             4.0  Throwbacks   
4        0.678   5.0  ...    0.734  138.009             4.0  Throwbacks   
...        ...   ...  ...      ...      ...             ...         ...   
809171   0.190   4.0  ...    0.326  125.319             4.0   Feel Good   
809172   0.535   4.0  ...    0.326  167.178             4.0   Feel Good   
809173   0.924   8.0  ...    0.725  154.961             4.0   Feel Good   
809174   0.412  11.0  ...    0.179  114.408             4.0   Feel Good   
809175   0.235   7.0  ...    0.378  199.894             4.0   Feel Good   

        Num_Tracks  Num_Albums  Num_Artists  Follow  Collab     Pid  
0               52          47           37       1   False       0  
1               52          47           37       1   False       0  
2               52          47           37       1   False       0  
3               52          47           37       1   False       0  
4               52          47           37       1   False       0  
...            ...         ...          ...     ...     ...     ...  
809171         149       

In [ ]:
df_mean_dates = pd.DataFrame(df_mean_date)
df_merged = pd.merge(df4, df_mean_dates, on='Track URI', how='left')
# drop the original date column
df_merged = df_merged.drop(columns=['Date_x'])
df_merged = df_merged.rename(columns={'Date_y':'Date'})
df_merged = df_merged.reindex(columns=['Track URI', 'Track', 'Artist', 'Album', 'Date', 'Duration', 'Genre',
       'Danceability', 'Energy', 'Key', 'Loudness', 'Mode', 'Speechiness',
       'Acousticness', 'Instrumentalness', 'Liveness', 'Valence', 'Tempo',
       'Time Signature', 'Playlist', 'Num_Tracks', 'Num_Albums', 'Num_Artists',
       'Follow', 'Collab', 'Pid'])
df_merged

Track URI             Track  \
0       spotify:track:6sqNctd7MlJoKDOxPVCAvU   My Happy Ending   
1       spotify:track:3BxWKCI06eQ5Od8TY2JBeA           Buttons   
2       spotify:track:34ceTg8ChN5HjrqiIYCn9Q  Miss Independent   
3       spotify:track:67T6l4q3zVjC5nZZPXByU8       Whatcha Say   
4       spotify:track:7H6ev70Weq6DdpZyyTmUXk       Say My Name   
...                                      ...               ...   
809171  spotify:track:64GRDrL1efgXclrhVCeuA0       Lay Me Down   
809172  spotify:track:4kdfjhj9xNkYU0R8xlDy8k             6 Man   
809173  spotify:track:2iUmqdfGZcHIhS3b9E9EWq   Everybody Talks   
809174  spotify:track:5InOp6q2vvx0fShv3bzFLZ     Know Yourself   
809175  spotify:track:7JXZq0JgG2zTrSOAgY8VMC            Jungle   

                    Artist                                 Album    Date  \
0            Avril Lavigne                         Under My Skin  2004.0   
1       The Pussycat Dolls                                   PCD  2008.0   
2                    Ne-Yo                 Year Of The Gentleman  2008.0   
3             Jason Derulo                          Jason Derulo  2013.0   
4          Destiny's Child             The Writing's On The Wall  1999.0   
...                    ...                                   ...     ...   
809171           Sam Smith                    In The Lonely Hour  2014.0   
809172               Drake  If You're Reading This It's Too Late  2016.0   
809173          Neon Trees                          Picture Show  2012.0   
809174               Drake  If You're Reading This It's Too Late  2016.0   
809175               Drake  If You're Reading This It's Too Late  2016.0   

        Duration                                       Genre  Danceability  \
0         242413                  canadian pop,candy pop,pop         0.414   
1         225560                                         RnB         0.570   
2         232000                                         RnB         0.673   
3         221253                                         RnB         0.615   
4         271333                                         RnB         0.713   
...          ...                                         ...           ...   
809171    219536                                         Emo         0.468   
809172    167653                                      Hiphop         0.568   
809173    177280  modern rock,neo mellow,pop rock,pov: indie         0.471   
809174    275840                                         Rap         0.720   
809175    320400                                         RnB         0.697   

        Energy   Key  ...  Valence    Tempo  Time Signature    Playlist  \
0        0.936   2.0  ...    0.740  170.229             4.0  Throwbacks   
1        0.821   2.0  ...    0.408  210.857             4.0  Throwbacks   
2        0.683   1.0  ...    0.713  171.860             4.0  Throwbacks   
3        0.711  11.0  ...    0.711  144.036             4.0  Throwbacks   
4        0.678   5.0  ...    0.734  138.009             4.0  Throwbacks   
...        ...   ...  ...      ...      ...             ...         ...   
809171   0.190   4.0  ...    0.326  125.319             4.0   Feel Good   
809172   0.535   4.0  ...    0.326  167.178             4.0   Feel Good   
809173   0.924   8.0  ...    0.725  154.961             4.0   Feel Good   
809174   0.412  11.0  ...    0.179  114.408             4.0   Feel Good   
809175   0.235   7.0  ...    0.378  199.894             4.0   Feel Good   

        Num_Tracks  Num_Albums  Num_Artists  Follow  Collab     Pid  
0               52          47           37       1   False       0  
1               52          47           37       1   False       0  
2               52          47           37       1   False       0  
3               52          47           37       1   False       0  
4               52          47           37       1   False       0  
...            ...         ...          ...     ...     ...     ...  
8

In [ ]:
# checking that the date was modified
df_merged[df_merged['Track URI']=='spotify:track:6sqNctd7MlJoKDOxPVCAvU']

Track URI            Track         Artist  \
0       spotify:track:6sqNctd7MlJoKDOxPVCAvU  My Happy Ending  Avril Lavigne   
21      spotify:track:6sqNctd7MlJoKDOxPVCAvU  My Happy Ending  Avril Lavigne   
16617   spotify:track:6sqNctd7MlJoKDOxPVCAvU  My Happy Ending  Avril Lavigne   
16622   spotify:track:6sqNctd7MlJoKDOxPVCAvU  My Happy Ending  Avril Lavigne   
23249   spotify:track:6sqNctd7MlJoKDOxPVCAvU  My Happy Ending  Avril Lavigne   
...                                      ...              ...            ...   
779012  spotify:track:6sqNctd7MlJoKDOxPVCAvU  My Happy Ending  Avril Lavigne   
781222  spotify:track:6sqNctd7MlJoKDOxPVCAvU  My Happy Ending  Avril Lavigne   
781224  spotify:track:6sqNctd7MlJoKDOxPVCAvU  My Happy Ending  Avril Lavigne   
792617  spotify:track:6sqNctd7MlJoKDOxPVCAvU  My Happy Ending  Avril Lavigne   
792650  spotify:track:6sqNctd7MlJoKDOxPVCAvU  My Happy Ending  Avril Lavigne   

                Album    Date  Duration                       Genre  \
0       Under My Skin  2004.0    242413  canadian pop,candy pop,pop   
21      Under My Skin  2004.0    242413                         Emo   
16617   Under My Skin  2004.0    242413                         Emo   
16622   Under My Skin  2004.0    242413  canadian pop,candy pop,pop   
23249   Under My Skin  2004.0    242413                         Emo   
...               ...     ...       ...                         ...   
779012  Under My Skin  2004.0    242413                         Emo   
781222  Under My Skin  2004.0    242413                         Emo   
781224  Under My Skin  2004.0    242413  canadian pop,candy pop,pop   
792617  Under My Skin  2004.0    242413  canadian pop,candy pop,pop   
792650  Under My Skin  2004.0    242413                         Emo   

        Danceability  Energy  Key  ...  Valence    Tempo  Time Signature  \
0              0.414   0.936  2.0  ...     0.74  170.229             4.0   
21             0.414   0.936  2.0  ...     0.74  170.229             4.0   
16617          0.414   0.936  2.0  ...     0.74  170.229             4.0   
16622          0.414   0.936  2.0  ...     0.74  170.229             4.0   
23249          0.414   0.936  2.0  ...     0.74  170.229             4.0   
...              ...     ...  ...  ...      ...      ...             ...   
779012         0.414   0.936  2.0  ...     0.74  170.229             4.0   
781222         0.414   0.936  2.0  ...     0.74  170.229             4.0   
781224         0.414   0.936  2.0  ...     0.74  170.229             4.0   
792617         0.414   0.936  2.0  ...     0.74  170.229             4.0   
792650         0.414   0.936  2.0  ...     0.74  170.229             4.0   

                 Playlist  Num_Tracks  Num_Albums  Num_Artists  Follow  \
0              Throwbacks          52          47           37       1   
21             Throwbacks          52          47           37       1   
16617   Dancing on my own         172          69           35       1   
16622   Dancing on my own         172          69           35       1   
23249                fall          67          55           46       1   
...                   ...         ...         ...          ...     ...   
779012           Sad :(((          70          63           47       1   
781222              Newer         184         124           73       1   
781224              Newer         184         124           73       1   
792617         2000s jams          70          53           34       1   
792650         2000s jams          70          53           34       1   

        Collab     Pid  
0        False       0  
21       False       0  
16617     True     987  
16622     True     987  
23249    False    1443  
...        ...     ...  
779012   False  141033  
781222   False  141180  
781224   False  141180  
792617   False  141938  
792650   False  141938  

[186 rows x 26 columns]

In [ ]:
df_merged['Date'] = df_merged['Date'].astype(int)
df4['Date'] = df4['Date'].astype(int)

# df_merged['Date'] = df_merged['Date'].astype(str)
# df4['Date'] = df4['Date'].astype(str)

In [ ]:
df_merged[df_merged['Date'] != df4['Date']]

Track URI  \
6       spotify:track:20ORwCJusz4KS2PbTPVNKo   
8       spotify:track:7DFnq8FYhHMCylykf6ZCxA   
9       spotify:track:7k6IzwMGpxnRghE7YosnXT   
10      spotify:track:7k6IzwMGpxnRghE7YosnXT   
11      spotify:track:1TfAhjzRBWzYZ8IdUV3igl   
...                                      ...   
809139  spotify:track:7m9OqQk4RVRkw9JJdeAw96   
809141  spotify:track:5tz69p7tJuGPeMGwNTxYuV   
809144  spotify:track:3bidbhpOYeV4knp8AIu8Xn   
809168  spotify:track:5TvE3pk05pyFIGdSY9j4DJ   
809170  spotify:track:2SiqlgLMfKQbczSMRp8drY   

                                   Track                   Artist  \
6                                Leavin'          Jesse McCartney   
8                    Yo (Excuse Me Miss)              Chris Brown   
9                                 Me & U                   Cassie   
10                                Me & U                   Cassie   
11                             Year 3000           Jonas Brothers   
...                                  ...                      ...   
809139                    Jocelyn Flores             XXXTENTACION   
809141                    1-800-273-8255                    Logic   
809144  Can't Hold Us - feat. Ray Dalton  Macklemore & Ryan Lewis   
809168                     Say Something        A Great Big World   
809170                    Into The Ocean             Blue October   

                                                    Album  Date  Duration  \
6                                   Departure - Recharged  2005    216880   
8                                             Chris Brown  2005    229040   
9                                                  Cassie  2005    192213   
10                                                 Cassie  2005    192213   
11                                         Jonas Brothers  2006    201960   
...                                                   ...   ...       ...   
809139                                                 17  2013    119133   
809141                                          Everybody  2013    250173   
809144                                          The Heist  2007    258343   
809168  Is There Anybody Out There? - Track by Track C...  2008    229400   
809170                                             Foiled  2005    239947   

                  Genre  Danceability  Energy   Key  ...  Valence    Tempo  \
6                   RnB         0.687   0.710   9.0  ...   0.8860  158.470   
8                   RnB         0.536   0.612   4.0  ...   0.5700  173.536   
9                   RnB         0.803   0.454   8.0  ...   0.7390  199.980   
10               Hiphop         0.803   0.454   8.0  ...   0.7390  199.980   
11                  Emo         0.659   0.869  11.0  ...   0.8110  106.966   
...                 ...           ...     ...   ...  ...      ...      ...   
809139  Underground Rap         0.872   0.391   0.0  ...   0.4370  134.021   
809141              Emo         0.620   0.574   5.0  ...   0.3570  200.046   
809144              Rap         0.641   0.922   2.0  ...   0.8470  146.078   
809168              Emo         0.407   0.147   2.0  ...   0.0765  141.284   
809170              Emo         0.758   0.606   0.0  ...   0.3610  107.950   

        Time Signature       Playlist  Num_Tracks  Num_Albums  Num_Artists  \
6                  4.0     Throwbacks          52          47           37   
8                  4.0     Throwbacks          52          47           37   
9                  4.0     Throwbacks          52          47           37   
10                 4.0     Throwbacks          52          47           37   
11                 4.0     Throwbacks          52          47           37   
...                ...            ...         ...         ...          ...   
809139             4.0  getting ready          27          27           21   
809141             4.0  getting ready          27          27           21   
809144             4.0      Feel Good         149          84    

In [ ]:
df4[df4['Track URI']=='spotify:track:3bidbhpOYeV4knp8AIu8Xn']

Track URI  \
91      spotify:track:3bidbhpOYeV4knp8AIu8Xn   
589     spotify:track:3bidbhpOYeV4knp8AIu8Xn   
1097    spotify:track:3bidbhpOYeV4knp8AIu8Xn   
2913    spotify:track:3bidbhpOYeV4knp8AIu8Xn   
3180    spotify:track:3bidbhpOYeV4knp8AIu8Xn   
...                                      ...   
805191  spotify:track:3bidbhpOYeV4knp8AIu8Xn   
805958  spotify:track:3bidbhpOYeV4knp8AIu8Xn   
806848  spotify:track:3bidbhpOYeV4knp8AIu8Xn   
808608  spotify:track:3bidbhpOYeV4knp8AIu8Xn   
809144  spotify:track:3bidbhpOYeV4knp8AIu8Xn   

                                   Track                   Artist      Album  \
91      Can't Hold Us - feat. Ray Dalton  Macklemore & Ryan Lewis  The Heist   
589     Can't Hold Us - feat. Ray Dalton  Macklemore & Ryan Lewis  The Heist   
1097    Can't Hold Us - feat. Ray Dalton  Macklemore & Ryan Lewis  The Heist   
2913    Can't Hold Us - feat. Ray Dalton  Macklemore & Ryan Lewis  The Heist   
3180    Can't Hold Us - feat. Ray Dalton  Macklemore & Ryan Lewis  The Heist   
...                                  ...                      ...        ...   
805191  Can't Hold Us - feat. Ray Dalton  Macklemore & Ryan Lewis  The Heist   
805958  Can't Hold Us - feat. Ray Dalton  Macklemore & Ryan Lewis  The Heist   
806848  Can't Hold Us - feat. Ray Dalton  Macklemore & Ryan Lewis  The Heist   
808608  Can't Hold Us - feat. Ray Dalton  Macklemore & Ryan Lewis  The Heist   
809144  Can't Hold Us - feat. Ray Dalton  Macklemore & Ryan Lewis  The Heist   

        Date  Duration Genre  Danceability  Energy  Key  ...  Valence  \
91      2003    258343   Rap         0.641   0.922  2.0  ...    0.847   
589     2010    258343   Rap         0.641   0.922  2.0  ...    0.847   
1097    2013    258343   Rap         0.641   0.922  2.0  ...    0.847   
2913    2015    258343   Rap         0.641   0.922  2.0  ...    0.847   
3180    2015    258343   Rap         0.641   0.922  2.0  ...    0.847   
...      ...       ...   ...           ...     ...  ...  ...      ...   
805191  2009    258343   Rap         0.641   0.922  2.0  ...    0.847   
805958  2013    258343   Rap         0.641   0.922  2.0  ...    0.847   
806848  2006    258343   Rap         0.641   0.922  2.0  ...    0.847   
808608  2014    258343   Rap         0.641   0.922  2.0  ...    0.847   
809144  2012    258343   Rap         0.641   0.922  2.0  ...    0.847   

          Tempo  Time Signature       Playlist  Num_Tracks  Num_Albums  \
91      146.078             4.0        Wedding          80          71   
589     146.078             4.0  Road Trippin'         158         131   
1097    146.078             4.0            Gym          72          63   
2913    146.078             4.0         Alexia          41          25   
3180    146.078             4.0   Bus playlist          52          41   
...         ...             ...            ...         ...         ...   
805191  146.078             4.0     randomness         162          70   
805958  146.078             4.0      Summerrrr          77          70   
806848  146.078             4.0         2000s.         139         115   
808608  146.078             4.0             32          20          20   
809144  146.078             4.0      Feel Good         149          84   

        Num_Artists  Follow  Collab     Pid  
91               56       1   False       5  
589             106       2   False      42  
1097             45       2   False      85  
2913             21       1   False     186  
3180             34       2   False     209  
...             ...     ...     ...     ...  
805191           80       1   False  142740  
805958           66       1   False  142786  
806848           75      17   False  142830  
808608           19       4   False  142975  
809144           62       1   False  142998  

[879 rows x 26 columns]

In [ ]:
df_merged[df_merged['Track URI']=='spotify:track:3bidbhpOYeV4knp8AIu8Xn'].iloc[0,:]

Track URI           spotify:track:3bidbhpOYeV4knp8AIu8Xn
Track                   Can't Hold Us - feat. Ray Dalton
Artist                           Macklemore & Ryan Lewis
Album                                          The Heist
Date                                                2007
Duration                                          258343
Genre                                                Rap
Danceability                                       0.641
Energy                                             0.922
Key                                                  2.0
Loudness                                          -4.457
Mode                                                 1.0
Speechiness                                       0.0786
Acousticness                                      0.0291
Instrumentalness                                     0.0
Liveness                                          0.0862
Valence                                            0.847
Tempo                          

In [ ]:
df_merged[df_merged['Track']=="wokeuplikethis*"].iloc[0,:]

Track URI           spotify:track:59J5nzL1KniFHnU120dQzt
Track                                    wokeuplikethis*
Artist                                     Playboi Carti
Album                                      Playboi Carti
Date                                                2014
Duration                                          235535
Genre                                                RnB
Danceability                                       0.785
Energy                                              0.62
Key                                                  8.0
Loudness                                          -6.667
Mode                                                 1.0
Speechiness                                        0.254
Acousticness                                      0.0138
Instrumentalness                                     0.0
Liveness                                            0.15
Valence                                            0.478
Tempo                          

Notice that Can't hold us appears 870 times. It's mean date is 2007, when it's actual date is 2012. In the previous imputation (on the unreplicated data), the imputed date was 2001. This is a much better improvement. Similarly, 'wokeuplikethis*' has an imputed date of 2014, which is very close to the actual date of 2017. We can assume our imputation gives a good approximation of the actual dates. 

A way to check that our imputation is correct, would be to delete the dates that we know are correct (the ones we had from the beginning), impute them and compare them with the originals.

## Final dataset with all the imputed dates for all the playlists

Then use the code to remove replicated data to obtain the dataset with only unreplicated values.

In [ ]:
df_merged.to_csv("playlists_with_dates.csv", index=False)